In [33]:
import torch

In [1]:
!wget https://s3.amazonaws.com/amazon-reviews-pds/tsv/amazon_reviews_us_Camera_v1_00.tsv.gz

--2020-10-15 18:48:56--  https://s3.amazonaws.com/amazon-reviews-pds/tsv/amazon_reviews_us_Camera_v1_00.tsv.gz
Resolving s3.amazonaws.com (s3.amazonaws.com)... 52.217.43.14
Connecting to s3.amazonaws.com (s3.amazonaws.com)|52.217.43.14|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 442653086 (422M) [application/x-gzip]
Saving to: ‘amazon_reviews_us_Camera_v1_00.tsv.gz’

amazon_reviews_us_C 100%[===================>] 422.15M  73.8MB/s    in 5.6s    

2020-10-15 18:49:01 (75.6 MB/s) - ‘amazon_reviews_us_Camera_v1_00.tsv.gz’ saved [442653086/442653086]



In [1]:
import pandas as pd
df = pd.read_csv("amazon_reviews_us_Camera_v1_00.tsv.gz",  sep='\t', compression='gzip', error_bad_lines=False, dtype='str')

b'Skipping line 85458: expected 15 fields, saw 22\nSkipping line 91161: expected 15 fields, saw 22\n'
b'Skipping line 166123: expected 15 fields, saw 22\n'
b'Skipping line 225458: expected 15 fields, saw 22\nSkipping line 229936: expected 15 fields, saw 22\nSkipping line 259297: expected 15 fields, saw 22\n'
b'Skipping line 284728: expected 15 fields, saw 22\nSkipping line 286334: expected 15 fields, saw 22\nSkipping line 293400: expected 15 fields, saw 22\nSkipping line 294415: expected 15 fields, saw 22\nSkipping line 308150: expected 15 fields, saw 22\nSkipping line 315022: expected 15 fields, saw 22\nSkipping line 315730: expected 15 fields, saw 22\nSkipping line 316071: expected 15 fields, saw 22\nSkipping line 326729: expected 15 fields, saw 22\n'
b'Skipping line 329101: expected 15 fields, saw 22\nSkipping line 333077: expected 15 fields, saw 22\nSkipping line 377031: expected 15 fields, saw 22\nSkipping line 389496: expected 15 fields, saw 22\nSkipping line 390486: expected 15 

In [2]:
df.dropna(inplace=True)
# df = df[ (df["review_body"].astype(str).str.len() >10) & (df["review_body"].astype(str).str.len() <=128)]
df = df[ (df["star_rating"] == "1") | (df["star_rating"] == "5")]
df = df[["review_body","star_rating"]]
df["star_rating"] =  df["star_rating"].astype(int)
df["star_rating"] =  df["star_rating"].apply(lambda x: 1 if x == 5 else 0)
df = df[:100_0000]
df.head()

review_body  star_rating
0                                                 ok            1
1          Perfect, even sturdier than the original!            1
3  Exactly what I wanted and expected. Perfect fo...            1
4  I will look past the fact that they tricked me...            1
7                        Great camera for the price.            1

In [3]:
df["star_rating"].value_counts()

1    868455
0    131545
Name: star_rating, dtype: int64

In [17]:
from sklearn.utils import resample
df_majority = df[df['star_rating']==1]
df_minority = df[df['star_rating']==0]

maj_class1 = resample(df_majority, replace=True,n_samples=len(df_minority))
df = pd.concat([maj_class1, df_minority])
df["star_rating"].value_counts()

1    131545
0    131545
Name: star_rating, dtype: int64

In [18]:
#BERT
import transformers
from transformers import BertModel, BertTokenizer, BertForSequenceClassification, AdamW, get_linear_schedule_with_warmup
import torch

import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, classification_report

from torch import nn, optim
from torch.utils.data import Dataset, DataLoader

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased', do_lower_case=True)


In [19]:
class ReviewDataset(Dataset):
    def __init__(self, reviews, targets, tokenizer):
        self.reviews = reviews
        self.targets = targets
        self.tokenizer = tokenizer
        self.max_length = 128

    def __len__(self):
        return len(self.reviews)

    def __getitem__(self, item):

        review = self.reviews.iloc[item]
        target = self.targets.iloc[item]
        encoding = self.tokenizer.encode_plus(
            review,
            add_special_tokens=True,
            max_length=self.max_length,
            pad_to_max_length=True,
            return_attention_mask=True,
            return_tensors='pt'
        )

        return {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'targets': torch.tensor(target, dtype=torch.long)
        }

In [20]:
df_train, df_test = train_test_split(
    df,
    test_size=0.2,
    random_state=42,
    stratify=df["star_rating"]
)

train_ds = ReviewDataset(reviews = df_train["review_body"], targets=df_train["star_rating"], tokenizer=tokenizer)
train_dl = DataLoader(train_ds, batch_size=32, num_workers=4)

test_ds = ReviewDataset(reviews = df_test["review_body"], targets=df_test["star_rating"], tokenizer=tokenizer)
test_dl = DataLoader(test_ds, batch_size=32, num_workers=4)


In [21]:
df_train["star_rating"].value_counts(), df_test["star_rating"].value_counts()

(1    105236
 0    105236
 Name: star_rating, dtype: int64,
 1    26309
 0    26309
 Name: star_rating, dtype: int64)

In [22]:
EPOCHS = 4
LEARNING_RATE = 3e-5

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Function to calculate the accuracy of our predictions vs labels
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
    return np.sum(pred_flat == labels_flat) / len(labels_flat)

def ret_model():
    model = BertForSequenceClassification.from_pretrained(
        "bert-base-uncased", 
        num_labels = 2, 
        output_attentions = False, 
        output_hidden_states = False,
    )
    return model

total_steps = len(train_dl) * EPOCHS

model = ret_model()
optim = AdamW(model.parameters(), lr=LEARNING_RATE, eps=1e-8)
scheduler = get_linear_schedule_with_warmup(optim, num_warmup_steps=0, num_training_steps=total_steps)

for epoch in range(0, EPOCHS):
    print("running epoch ",epoch)
    model = ret_model()
    model.to(device)
    total_loss = 0
    model.train()
    for step, batch in enumerate(train_dl):
        input_ids = batch["input_ids"].to(device)
        input_mask = batch["attention_mask"].to(device)
        labels = batch["targets"].to(device)

        model.zero_grad()
        loss, logits = model(input_ids, 
                        token_type_ids=None,
                        attention_mask = input_mask,
                        labels = labels)
        total_loss+= loss.item()
        loss.backward()
        
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)


        optim.step()
        scheduler.step()
        
    avg_train_loss = total_loss / len(train_dl)
    print("avg_train_loss",avg_train_loss)
    model.eval()
    
    total_eval_acc = 0
    total_eval_loss = 0
    eval_steps = 0

    for batch in test_dl:
        input_ids = batch["input_ids"].to(device)
        input_mask = batch["attention_mask"].to(device)
        labels = batch["targets"].to(device)

        with torch.no_grad():
            loss, logits = model(input_ids, 
                        token_type_ids=None,
                        attention_mask = input_mask,
                        labels = labels)

        total_eval_loss+= loss.item()
        logits = logits.detach().cpu().numpy()
        label_ids = labels.to("cpu").numpy()
        total_eval_acc += flat_accuracy(logits, label_ids)


    avg_val_acc = total_eval_acc / len(test_dl)
    print("  Accuracy: {0:.2f}".format(avg_val_acc))
    
    avg_val_loss = total_eval_loss / len(test_dl)
    print("  Validation Loss: {0:.2f}".format(avg_val_loss))


running epoch  0
avg_train_loss 0.7183231116700368
  Accuracy: 0.52
  Validation Loss: 0.72
running epoch  1
avg_train_loss 0.7506695316804872
  Accuracy: 0.50
  Validation Loss: 0.75
running epoch  2
avg_train_loss 0.6988484475361826
  Accuracy: 0.51
  Validation Loss: 0.69
running epoch  3
avg_train_loss 0.7250909293883113
  Accuracy: 0.51
  Validation Loss: 0.73


In [23]:
torch.save(model.state_dict(), "model.pth")

In [24]:
model = ret_model()
model.load_state_dict(torch.load("model.pth"))
model.eval()
print("")

In [65]:
def detect_sentiment(sentence):
    inputs = tokenizer.encode_plus(
                sentence,
                add_special_tokens=True,
                max_length=128,
                return_token_type_ids=True,
                pad_to_max_length=True,
                return_attention_mask=True,
                return_tensors='pt'
            )
#     print(inputs)
    ids = inputs["input_ids"]
    mask = inputs["attention_mask"]
    token_type_ids = inputs["token_type_ids"]

    outputs = model(ids, token_type_ids=token_type_ids, attention_mask=mask)
    # outputs
    preds = torch.sigmoid(outputs[0]).cpu().detach().numpy()
#     print(preds)
    # preds
    return np.argmax(preds, axis=1)

In [66]:
detect_sentiment("this is terrible")

array([0])

In [67]:
detect_sentiment("Works GREAT and is FAST!  Thanks!  I love using it with firewire!  Makes image transfer from my SD cards speedy!")

array([0])

In [59]:
df[df["star_rating"] == 1].iloc[40]["review_body"]

'very satisfied fast delivery would recommend ,charges  fast'

In [63]:
pos_reviews = df[df["star_rating"] == 1]
for index, row in pos_reviews.iterrows():
    print(row["review_body"])

Exactly what we need
very pleased with the barlow len will order more len's soon
Thanks for having an extra battery, I could take as many pics as I wanted of our grandson's game. Afterwards there was a celebration and with a car charger (I have not had to use yet) I knew that if I'd went through both batteries I could recharge easily!!
great product expecially since the gopro doesnt come with a wall charger. the led light lets you know when the battery is charged. i only wish the gopro batteries would last longer when filming in hd. but thast why i have 3 batteries now!
My other lenses have hoods that simply click into place, and then twist to release/remove.  This one has an actual button to release it for removal.  Very high-grade material, feels solid.  It is freakin huge though, makes an already big lens much bigger.  Its diameter is quite big relative to the diameter of the lens itself for some reason.  As an example, when I reverse the hood on my 105mm Nikon lens, there is not mu

This strap is far superior to your basic camera strap. Not only does it allow for easier use, it is adjustable to fit perfectly. It never gets in the way like other straps do and is a pleasure to use. Item arrived on time and with no problems. The condition was as listed and works perfectly. Would definitely recommend the seller.
In today's slam-dunk on the go world, stuff happens. Stuff happens to expensive stuff. Enter the Accident Protection Plan. I hope we won't need it, but it's there if we do.
they work very well
Too bad it's not a constant aperture!
wow, great!
Its a brilliant Grip and looks good on the camera. It is well made and a fraction of the price of a Leica Handgrip, it is also individual.  It is made to fit over the bottom of the camera so unlike the Leica one you dont have to remove the base. I like it very much and even with duty (I live in UK) it is well worth it and recommend it to all.
Is a greath camera I take good pics and Im ver y happy with it<br />The only pro

Good company - good communication.  That's important.  Item is right on.
Just what I was looking for
These are great to have since I have multiple DSLR's and lenses with tri/mono mount rings.  Its easier just to have a couple extra on hand and for the price there's no reason not to have some spares.
I'm a Pentax &#34;lover&#34;, so I like the camera.
I have only used it a couple of times now, but each time I have been able to record for more then 4 hours with more then half the battery life still showing on the GoPro.  This is a great battery.  The housing that came with it though, did not seem to fit that easily.  It snaps on and closes, but there is a gap unless I squeeze it closed and then clasp it closed.  I don't know how much I trust the backdoor.  I wish they made a frame housing for it too.  Maybe they will at some point, but the ones you get from GoPro does not fit with this battery since it's bigger then just having a backpack on it.
I have only had the camera for about a wee

I got this for my Kodak C875 camera.  I did the water test with a tissue inside and no leaks.  Just a little hard to extend the zoom and cannot zoom out all the way.  Otherwise, just fine.  Am looking forward to using it on a cruise.
This is a wonderful way to get your flash off camera. And operating your flash in manual mode can create some striking images. It has never missed a pop.
Work exactly as they should, no issues so far.  These really help soften harsh direct lighting.<br />I used these to dampen the light out of floodlight based stage lighting.
Awesome camera and value.
Best the that ever happen to me when I receive this cord
This is THE camera bag of all camera bags because there is so much room in this beautiful baby. Holds it all in there and keeps it very well contained and safe.
Excellent little light weight camera for FPV on a 250 quad or other RC aircraft. It provides a better image than the stock 480 TVL camera that came with my Quanum DIY FPV kit.
This is a great pr

Great camera and easy to use.....
Holy %^#*! This is AMAZING! I'm constantly annoyed by smudgy lenses on my readers and sunglasses, and I'd more or less given up hope of finding a real solution beyond endless wiping---so when this arrived, I hoped but didn't expect too much from it. Wow I was so wrong! Two little squirts and a quick buff with the *miracle* cloth, and my readers were as clean as when I'd first purchased them. AND they stayed clean all day, another miracle. I'm so excited and happy to finally have a way to see clearly that I'm buying a couple more sets so I'll have them with me everywhere I go.
terrific system. Does everything it says it will do. Would definitely recommend it
Very nice camera.  It works well for what I use it for, it does some nice close ups but you got to be patient and wait for it to focus to get great photos, glad I bought it.
love it
love it
This screen cover was a snap to out on the viewfinder...before applying it I was constantly cleaning smudges, 

...

I take my Nikon L820 EVERYWHERE; hiking, biking, exploring,... these screen protectors are the best deal on the net  :-D
exactly what was described, the air puffer could be better but overall good product. I would recommend it to a friend.
Very pleased with this remote.<br /><br />In a total of two minutes I took it out of it's package, inserted the battery, set my NEX 7 to 'remote' and was snapping pictures with it successfully.<br />It comes with video start and 2 second timer buttons as well.<br />The camera's shutter button still works in 'remote' mode in case you need to use it. No issues whatsoever with this remote.<br /><br />Awesome product for the price!!
looks very nice witha nice packing fits my Nikon as charm ..and yea one of the best customer service ever thanks alot.
I was pleased with the quality of the pictures taken above the water.  It took great pictures in the pool.  I still have not used all of the functions of the camera, as I received it right before our vacation

still working fine
Great value for the money spent. Loved each product... I really needed this kit and it has made life behind the lens so much easier...
we0rks perfect
I have been using these batteries in my Canon Powershot SX510 HS over the last month. The battery performance is amazing, based on my real-world usage I've found that these batteries actually outperform the OEM battery that came with the camera. Highly recommended if you need a replacement, or spare.
Price was decent, it does everything I wanted and expected in a quality camera, plus the extras included sealed the deal for me -  especially the extra battery and memory card.
It is what I ordered. Good construction too. Not much more I can say about this product. Okay I love it...lol
This is a Pretty good and well made mount. Best quality! The price is afordable. Will probably buy again soon!
It works well for what we needed it for. We mounts the camera on the roll bar of our pulling tractor.<br />Excellent picture and so

Purchased for my Samsung HMX-300,this battery fits and works as described.It slightly thinner in depth from the OEM Samsung,and thus,is a bit more recessed when installed.Not a problem for me.The output is the same on the tag,and as of now,I haven't tested the run time.It should be comparable to the OEM.Overall,I find it a great buy!
Product as promised.  A very nice, suitable, and inexpensive replacement to the originals. You couldn't ask for more for the price you pay.
If you are a camera user, you are going to use it with the special strap. Best bang for the buck
This Fotodiox lens hood fit my Canon 135mm ƒ/2L just fine. Way less money than buying from Canon. What more could you want?
with my family needed a camera and allowed us to make this purchase photographs of our vacation in disney world, thank you very much
This item was a great price, delivered very quickly and works perfectly. Very happy with this seller and this product! I will definitely check their other items when I ne

A great chest harness. I have got some great footage zip lining, running, kayaking, etc while my ASV100 was mounted to this! Well made and put together.
I can't say enough about the Yongnuo, except that I don't think its guide rating of 58 is exactly correct. Aside from being a little less powerful then I would think it should be (I have no inclination to test the guide number rating), this flash is excellent. It's well constructed (looks like a Canon design), recharges quickly if not used at full power and is fairly easy to set up and understand, even without the instructions (they were included). I purchased two of them for practicing off camera flash photography and to add some creativity to my amateur work. I am extremely happy with the purchase and would recommend them to anyone (along with their wireless triggers) that wants to delve into off camera flash photography but doesn't want to break the bank buying name brand i-ttl flashes like the SB-900 for Nikon or their Canon equiva

KeyboardInterrupt: 